# Setup

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import csv
import json
import string
import random
import queue
import threading
from pprint import pprint
import numpy as np
from typing import List
from retry import retry
from distutils.util import strtobool
from sentence_transformers import SentenceTransformer, util

In [4]:
from greyparrot.chats_common import PartialChat
from greyparrot.multi_tenancy.v3_config import V3Config
from greyparrot.conversations.db import ConversationsDBConn
from greyparrot.llm.prompting import prompts as prompts_utils
from greyparrot.llm.utils import AZURE_SUBDOMAIN_TO_API_KEY, get_azure_subdomain_from_model
from llm_proxy import get_open_ai_client, LLMProxyProperties
from greyparrot.discovery import IntentDiscovery, IntentDiscoveryStrategy
from greyparrot.discovery.intents.common import DiscoveredIntent
from greyparrot.common.utils import get_timestamp_as_version
from greyparrot.conversations.utils import get_chats
from greyparrot.dataset_common import Dataset

Using local gitdb: /src/config/


In [5]:
from greyparrot.common import get_logger

logger = get_logger(__name__)

In [6]:
embedder = SentenceTransformer('all-mpnet-base-v2')

In [7]:
customer_id = 'brinks'
profile_id = 'care-voice'
usecase_id = 'care-voice'
language_code = 'en-US'
customer_name = V3Config.short_name_from_ids(customer_id, profile_id)
customer_name

'brinks-care-voice'

In [8]:
def get_chats_with_ids(chat_ids: List[str]):
    customer_name = V3Config.short_name_from_ids(customer_id, profile_id)
    conv_db_conn = ConversationsDBConn.from_customer_name(customer_name)
    chats = conv_db_conn.get_detailed_chats(
        customer_id=customer_id,
        profile_id=profile_id,
        usecase_id=usecase_id,
        language_code=language_code,
        conversation_ids=chat_ids,
        is_dev_user=False,
    )
    return chats

In [9]:
LLM_ENGINE = 'gpt-4-0125-preview'
USE_AZURE = False
CONCURRENCY = 10

In [10]:
llm_proxy_properties = LLMProxyProperties(
    project_id="virtual-agent-simulation",
    customer_id=customer_id,
    profile_id=profile_id,
    usecase_id="",
)
if USE_AZURE:
    print('Using AzureOpenAI!')
    azure_subdomain = get_azure_subdomain_from_model(LLM_ENGINE)
    open_ai_client = get_open_ai_client(
        llm_proxy_properties=llm_proxy_properties,
        provider="openai",
        use_azure=True,
        azure_subdomain=azure_subdomain,
        api_key=AZURE_SUBDOMAIN_TO_API_KEY[azure_subdomain],
    )
else:
    print('Using OpenAI!')
    open_ai_client = get_open_ai_client(
        llm_proxy_properties=llm_proxy_properties,
        provider="openai",
    )

Using OpenAI!


In [11]:
@retry(tries=3, delay=60, backoff=2, logger=logger)
def chat_completion(**kwargs):
    return open_ai_client.chat.completions.create(**kwargs)

In [200]:
def save_jsonl_file(data, output_file):
    with open(output_file, 'w') as f:
        for item in data:
            f.write(json.dumps(item) + "\n")

In [198]:
def print_workflow(w: dict):    
    for w_k, w_v in w.items():        
        if isinstance(w_v, list):
            val = '\n* '.join(w_v)
            print(f'{w_k.capitalize()}:\n* {val}')
        else:
            print(f'{w_k.capitalize()}: {w_v}')
    print('-' * 50)

# Discovery prompts

In [12]:
# TODO remove this after fixing speaker_role flips
flips = {'agent': 'visitor', 'visitor': 'agent'}

In [13]:
def chat_to_prompt_text(chat: PartialChat, speakers_flipped: bool = False):
    return '\n'.join([
        f'{string.capwords(prompts_utils.speaker_role_str_for_prompts(flips[m.speaker_role.value] if speakers_flipped else m.speaker_role.value))}: {m.text}'
        for m in chat.messages
    ])

In [14]:
SYSTEM_PROMPT_AGENT_WORKFLOW_DISCOVERY = """### Context and data description
You are a conversation analyst working for a Call Center.

You will be given 1 conversation at a time. Each conversation is between a Call Center Agent and a Customer. Your primary goal is to generate a workflow of steps which Agent takes in **the given conversation** to help resolve the Customer's needs.

The primary use case of this this workflow is to create a template to address similar customer needs in the future.

The workflow should be a list of steps which the Agent needs to take.

The schema of each workflow should be as follows:
- **title**: title of the workflow
- **steps**: a list of steps which Agent needs to follow

**Important**: There could be more than 1 workflows in a single conversation. The workflows will be used create templates to address similar customer needs in the future."""

In [15]:
SYSTEM_PROMPT_VISITOR_WORKFLOW_DISCOVERY = """### Context and data description
You are a conversation analyst working for a Call Center.

You will be given 1 conversation at a time. Each conversation is between a Call Center Agent and a Customer. Your primary goal is to generate a flow of steps which Customer takes in **the given conversation**.

The primary use case of this this flow is to create a template to simulate similar customer scenarios.

The flow should be a list of steps which the Customer takes.

The schema of each flow should be as follows:
- **title**: title of the flow
- **steps**: a list of steps which Customer needs to follow

**Important**: There could be more than flows in a single conversation. The flows will be used create templates to simulate similar customer scenarios."""

In [16]:
SYSTEM_PROMPT_PARSE_WORKFLOW = """Convert the following list of workflows into a json output with keys:
- "title": string
- "steps": List[string]"""

In [17]:
FLOW_PROMPTS = {
    'agent': SYSTEM_PROMPT_AGENT_WORKFLOW_DISCOVERY,
    'visitor': SYSTEM_PROMPT_VISITOR_WORKFLOW_DISCOVERY
}

In [18]:
def discover_flow_in_chat(chat: PartialChat,
                          speaker_role: str,
                          speakers_flipped: bool = False,
                          llm_engine: str = LLM_ENGINE):
    logger.info(f'Discovering {speaker_role} flow in chat {chat.chat_name}')
    messages = [
        {
            "role": "system",
            "content": FLOW_PROMPTS[speaker_role]
        },
        {
            "role": "user",
            "content": chat_to_prompt_text(chat, speakers_flipped)
        },
    ]

    # Note: temperature=0.1 to allow for some exploration
    response = chat_completion(model=llm_engine,
                               messages=messages,
                               temperature=0.1,
                               top_p=1.0,
                               max_tokens=2048,
                               n=1)
    res_workflow_str = response.choices[0].message.content

    messages = [{
        "role": "system",
        "content": SYSTEM_PROMPT_PARSE_WORKFLOW
    }, {
        "role": "user",
        "content": res_workflow_str
    }]

    # TODO need a separate open_ai_client for mini if using Azure
    response = chat_completion(model='gpt-4o-mini-2024-07-18',
                               messages=messages,
                               temperature=0.0,
                               top_p=1.0,
                               max_tokens=2048,
                               n=1,
                               response_format={"type": "json_object"})
    parsed_workflow_str = response.choices[0].message.content

    # TODO define a JSON schema and handle this to make sure the required structure is respected
    parsed_workflows = json.loads(parsed_workflow_str)
    if isinstance(parsed_workflows, list):
        return parsed_workflows
    elif isinstance(parsed_workflows, dict):
        if len(parsed_workflows.keys()) == 1:
            return parsed_workflows[list(parsed_workflows.keys())[0]]
        else:
            return [parsed_workflows]

In [93]:
def extract_flows_from_chats(chats: List[PartialChat], speaker_role: str,
                                concurrency: int = 10):
    lock = threading.Lock()
    indexes = queue.Queue()

    workflows = {}
    for idx in range(len(chats)):
        indexes.put(idx)

    def workflow_labeler_worker():
        while True:
            try:
                idx = indexes.get(block=False)
            except queue.Empty:
                return
            chat = chats[idx]
            try:
                extracted_workflows = discover_flow_in_chat(chat, speaker_role)
                with lock:
                    workflows[str(chat)] = extracted_workflows
                    if len(workflows) % 10 == 0:
                        print(f'Workflows from {len(workflows)} chats extracted!')
            except Exception as e:
                logger.warning(e, str(chat))
            indexes.task_done()

    logger.info(
        f'Starting processing {len(chats)} chats with {concurrency} workers')
    workers = [
        threading.Thread(target=workflow_labeler_worker)
        for _ in range(concurrency)
    ]
    for worker in workers:
        worker.start()
    for worker in workers:
        worker.join()
    logger.info(f'Finished processing all {len(chats)} chats')

    return workflows

In [20]:
test_chat = get_chats_with_ids(['0843c54c-6487-45ce-946a-cc6257484f54'])[0]
str(test_chat), test_chat.messages

{"message": "use case id not set, fallback to use profile id care-voice", "name": "greyparrot.common.customers", "asctime": "2024-08-27 23:35:12", "levelname": "WARNING", "filename": "customers.py", "funcName": "__init__", "threadName": "MainThread", "status": "WARNING"}
{"message": "use case id not set, fallback to use profile id care-voice", "name": "greyparrot.common.customers", "asctime": "2024-08-27 23:35:14", "levelname": "WARNING", "filename": "customers.py", "funcName": "__init__", "threadName": "MainThread", "status": "WARNING"}


cmd: cresta-cli connstring -i voice-prod voice-prod brinks-care-voice-FKrGHU -r
cmd: cresta-cli connstring -i voice-prod voice-prod brinks-care-voice -r


('0843c54c-6487-45ce-946a-cc6257484f54',
 [[1704216964.443] agent (52e8889cd7b96083): Technical support,
  [1704216966.622] visitor (52e8889cd7b96083): Thank you for being the best part of Brinks Home. My name is Juan. Who do I have the pleasure of speaking with?,
  [1704216972.683] agent (52e8889cd7b96083): Debbie. Deborah Terryya.,
  [1704216974.782] visitor (52e8889cd7b96083): Good morning, missus Deborah. How can I assist you?,
  [1704216978.323] agent (52e8889cd7b96083): Okay. On December 16th, I had Brinks installed. I had one. Camera put on my front door, and I had one put on the tireport, and then I went out of town for a couple weeks. And only my carport has been working since December 6th eight. And I clicked on the troubleshoot for my front door, and it just keeps coming up that there's a problem. I mean, I did I did everything it told me to do. I unplugged the power cord, and told me to wait 5 minutes. And it was trying to find what the problem was. And it is still not resp

In [21]:
workflows = discover_flow_in_chat(test_chat, 'agent', speakers_flipped=True)
for idx, w in enumerate(workflows):
    print('-' * 50)
    print(f'[Agent Workflow#{idx + 1}]')
    for k, v in w.items():
        if isinstance(v, list):
            val = '\n* '.join(v)
            print(f'{k.capitalize()}:\n* {val}')
        else:
            print(f'{k.capitalize()}: {v}')

{"message": "Discovering agent flow in chat 0843c54c-6487-45ce-946a-cc6257484f54", "name": "__main__", "asctime": "2024-08-27 23:35:17", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "MainThread", "status": "INFO"}


--------------------------------------------------
[Agent Workflow#1]
Title: Troubleshooting a Non-Responsive Security Camera
Steps:
* Greet the customer warmly and introduce yourself.
* Ask for the customer's name for a personal touch.
* Verify the customer's account by asking for their phone number, full address, and verbal password.
* Confirm the customer's email address for further communication if needed.
* Ask the customer to describe the problem they are facing with their security camera.
* Clarify which camera (location-wise) is having the issue to ensure you are troubleshooting the correct device.
* Instruct the customer to check the LED light on the problematic camera to assess its status.
* If there's no light, guide the customer to check the power supply by unplugging the camera.
* Wait for about 30 seconds to 1 minute before plugging the camera back in to reset it.
* Ask the customer to check the LED light again for any changes.
* If the camera still shows no signs of powe

In [22]:
len(workflows)

2

# Relevant chats (from KA-QE trainset)

In [23]:
qe_dataset = Dataset.pull_from_repo(
    'brinks-care-voice/hf:082720241521675544.train')
len(qe_dataset)

{"message": "Pulling dataset brinks-care-voice/hf:082720241521675544.train from repo", "name": "dataset-common", "asctime": "2024-08-27 23:36:51", "levelname": "INFO", "filename": "common.py", "funcName": "pull_from_repo", "threadName": "MainThread", "status": "INFO"}
{"message": "use case id not set, fallback to use profile id care-voice", "name": "greyparrot.common.customers", "asctime": "2024-08-27 23:36:51", "levelname": "WARNING", "filename": "customers.py", "funcName": "__init__", "threadName": "MainThread", "status": "WARNING"}
{"message": "Loading dataset from s3://cresta-data-pci/brinks-care-voice/hf/082720241521675544.train", "name": "dataset-common", "asctime": "2024-08-27 23:36:52", "levelname": "INFO", "filename": "common.py", "funcName": "load", "threadName": "MainThread", "status": "INFO"}
{"message": "Loading dataset succeeded!", "name": "dataset-common", "asctime": "2024-08-27 23:36:56", "levelname": "INFO", "filename": "common.py", "funcName": "load", "threadName": "M

6157

In [24]:
qe_dataset[0]

(a37ae6b3-d890-44c8-add6-3efb94e36244[:14],
 'How to stop double drafting by ADT and Brinks for alarm system?')

In [25]:
chat_ids = list(set([pc.chat_name for pc, _ in qe_dataset]))
len(chat_ids)

2369

In [26]:
queries_to_chat = {query: pc.chat_name for pc, query in qe_dataset}

In [38]:
queries = list(queries_to_chat.keys())
len(queries)

5989

In [28]:
source_embeddings = embedder.encode(queries,
                                    convert_to_tensor=True,
                                    show_progress_bar=False)
len(source_embeddings)

5989

In [36]:
with open('Brinks Evaluation v.20240806_ - Response Evaluation (internal).csv',
          "r") as f:
    reader = csv.DictReader(f)
    data = list(reader)
    customer_queries = [entry["Question"] for entry in data]
len(customer_queries)

51

In [40]:
matched_queries = []
for q in customer_queries:
    target_embeddings = embedder.encode(q,
                                        convert_to_tensor=True,
                                        show_progress_bar=False)
    scores = util.cos_sim(target_embeddings,
                          source_embeddings).cpu().tolist()[0]
    matches = [(idx, score) for idx, score in enumerate(scores) if score > 0.7]
    if matches:
        matched_queries.extend([queries[i] for i, s in matches])

In [41]:
len(matched_queries)

75

In [43]:
matched_chats = [queries_to_chat[q] for q in matched_queries]
len(matched_chats)

75

In [46]:
num_chats = 1000
sampled_chat_ids = list(set(random.sample(chat_ids, num_chats) + matched_chats))
print(len(sampled_chat_ids))
sampled_chats = get_chats_with_ids(sampled_chat_ids)
len(sampled_chats)

1042


{"message": "use case id not set, fallback to use profile id care-voice", "name": "greyparrot.common.customers", "asctime": "2024-08-27 23:50:32", "levelname": "WARNING", "filename": "customers.py", "funcName": "__init__", "threadName": "MainThread", "status": "WARNING"}
{"message": "use case id not set, fallback to use profile id care-voice", "name": "greyparrot.common.customers", "asctime": "2024-08-27 23:50:34", "levelname": "WARNING", "filename": "customers.py", "funcName": "__init__", "threadName": "MainThread", "status": "WARNING"}


cmd: cresta-cli connstring -i voice-prod voice-prod brinks-care-voice-FKrGHU -r
cmd: cresta-cli connstring -i voice-prod voice-prod brinks-care-voice -r


1042

# Agent Workflow Discovery

In [ ]:
workflows = extract_flows_from_chats(sampled_chats, 'agent')

{"message": "Starting processing 1042 chats with 10 workers", "name": "__main__", "asctime": "2024-08-27 23:51:13", "levelname": "INFO", "filename": "2872213784.py", "funcName": "extract_workflow_from_chats", "threadName": "MainThread", "status": "INFO"}
{"message": "Discovering agent flow in chat 00001ce5-86b1-4a85-867e-a95d15538865", "name": "__main__", "asctime": "2024-08-27 23:51:13", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-6 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat 00059bd9-dfde-4710-be56-5b7baf1931e0", "name": "__main__", "asctime": "2024-08-27 23:51:13", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-7 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat 00523c8b-0189-4ac2-a34e-93abdeafa478", "name": "__main__", "asctime": "2024-08-27 23:51:13", "levelname": "INFO",

Workflows from 10 extracted!


{"message": "Discovering agent flow in chat 049c2d1b-f742-4e46-be75-28473a622425", "name": "__main__", "asctime": "2024-08-27 23:51:44", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-11 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat 057f639a-e82f-4bf2-95c1-03aafb420771", "name": "__main__", "asctime": "2024-08-27 23:51:45", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-6 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat 05e10909-2844-4710-beaa-bb85e5f6f18c", "name": "__main__", "asctime": "2024-08-27 23:51:46", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-8 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat 05fe2dce-903f-4d3f-a046-e697c9b4a674", "name": "__main__", "asctime": "20

Workflows from 20 extracted!


{"message": "Discovering agent flow in chat 06c18913-c1e4-4274-aed8-d9d9c0ce6528", "name": "__main__", "asctime": "2024-08-27 23:52:03", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-8 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat 06c7a277-4b56-40ef-be87-ffa95c1388d6", "name": "__main__", "asctime": "2024-08-27 23:52:06", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-9 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat 072722c1-d4b5-48e1-91be-c6311665f577", "name": "__main__", "asctime": "2024-08-27 23:52:06", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-6 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat 073fc9c1-6885-4f6d-b0b0-4ae4f6a2753b", "name": "__main__", "asctime": "202

...

{"message": "Discovering agent flow in chat c202c7ed-e36a-4002-af6e-f92a4f963097", "name": "__main__", "asctime": "2024-08-28 00:19:39", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-6 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat c214b170-d5c7-459f-a074-f289cd24dc15", "name": "__main__", "asctime": "2024-08-28 00:19:42", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-8 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat c2726aed-9c41-4f70-8929-9e5a1b0cd1b7", "name": "__main__", "asctime": "2024-08-28 00:19:43", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-9 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat c2bb6896-a430-41ec-85bd-42c22fa17874", "name": "__main__", "asctime": "202

Workflows from 830 extracted!


{"message": "Discovering agent flow in chat c46508ef-5312-40f6-b757-0ff2c24e40d2", "name": "__main__", "asctime": "2024-08-28 00:20:02", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-13 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat c4c219b2-81aa-4fae-9836-5725e36cc224", "name": "__main__", "asctime": "2024-08-28 00:20:02", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-15 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat c4c67546-8ef9-42d0-8926-f8b1c66dce7d", "name": "__main__", "asctime": "2024-08-28 00:20:02", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-10 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat c4cd95e3-1964-4270-a231-a9d95b4e5f99", "name": "__main__", "asctime": "

Workflows from 840 extracted!


{"message": "Discovering agent flow in chat c86e68d0-1127-416e-a190-76c0fcee3344", "name": "__main__", "asctime": "2024-08-28 00:20:12", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-15 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering agent flow in chat c8ae38f5-f5ce-4183-be01-590b2accbd64", "name": "__main__", "asctime": "2024-08-28 00:20:17", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-10 (workflow_labeler_worker)", "status": "INFO"}


In [52]:
len(workflows)

1042

In [42]:
for pc, ws in list(workflows.items())[:5]:
    print(f'\n\n<{pc}>')
    for idx, w in enumerate(ws):
        print('-' * 50)
        print(f'[Agent Workflow#{idx + 1}]')
        for k, v in w.items():
            if isinstance(v, list):
                val = '\n* '.join(v)
                print(f'{k.capitalize()}:\n* {val}')
            else:
                print(f'{k.capitalize()}: {v}')



<010c0ecf-e945-46c4-b11a-28bf1136225a>
--------------------------------------------------
[Agent Workflow#1]
Title: Setting Up New Security Codes for Employees
Steps:
* Greet the Customer: Start the conversation by thanking the customer for calling and introducing yourself.
* Identify the Customer's Need: Confirm the customer's request to set up new security codes for their employees.
* Clarify the Number of Codes Needed: Verify the number of new codes required by the customer.
* Collect Customer Verification Information: Ask for the customer's first and last name, request the verbal password associated with the account, and confirm the location address associated with the account to ensure accuracy.
* Gather Necessary Information: Inform the customer that you are collecting the required information for setting up new codes.
* Engage Technical Support: Notify the customer that assistance from the tech department will be needed to complete their request.
* Confirm Customer's Location:

In [97]:
title_to_workflow, title_to_pc_id = {}, {}
for pc_id, ws in workflows.items():
    for idx, w in enumerate(ws):
        title_to_workflow[w['title']] = w
        title_to_pc_id[w['title']] = pc_id

In [98]:
len(title_to_workflow), len(title_to_pc_id)

(1822, 1822)

In [62]:
def group_semantically_similar_workflows(workflows: List[str], embedder: SentenceTransformer,
                                           semantic_threshold: int = 0.8):
    workflow_embeddings = embedder.encode(workflows, convert_to_tensor=True)
    workflow_groups, solo_workflows = [], []
    for idx, workflow in enumerate(workflows):
        existing_groups = [group for group in workflow_groups if idx in group]
        if existing_groups:
            assert len(
                existing_groups) == 1, 'A workflow should only be in 1 group'
            continue

        print(f"Finding similar Workflows for Workflow#{idx}")

        scores = util.cos_sim(workflow_embeddings[idx:idx + 1],
                              workflow_embeddings).cpu().tolist()[0]
        matches = [
            i for i, score in enumerate(scores) if score > semantic_threshold
        ]
        filtered_matches = [i for i in matches if i != idx]
        if filtered_matches:
            outstanding_groups = []
            new_group = filtered_matches + [idx]
            for group in workflow_groups:
                if set(filtered_matches).intersection(set(group)):
                    new_group.extend(group)
                else:
                    outstanding_groups.append(group)
            workflow_groups = outstanding_groups + [list(set(new_group))]
        else:
            solo_workflows.append(idx)

    print(f'Found {len(solo_workflows)} # of Solo Workflows..')
    print(f'Found {len(workflow_groups)} # Groups of Workflows..')

    return [workflows[idx] for idx in solo_workflows
           ], [[workflows[idx] for idx in group] for group in workflow_groups]

In [64]:
solo_workflows, grouped_workflows = group_semantically_similar_workflows(
    list(title_to_workflow.keys()), embedder)

Finding similar Workflows for Workflow#0
Finding similar Workflows for Workflow#1
Finding similar Workflows for Workflow#2
Finding similar Workflows for Workflow#3
Finding similar Workflows for Workflow#5
Finding similar Workflows for Workflow#6
Finding similar Workflows for Workflow#7
Finding similar Workflows for Workflow#8
Finding similar Workflows for Workflow#9
Finding similar Workflows for Workflow#10
Finding similar Workflows for Workflow#11
Finding similar Workflows for Workflow#12
Finding similar Workflows for Workflow#14
Finding similar Workflows for Workflow#15
Finding similar Workflows for Workflow#16
Finding similar Workflows for Workflow#17
Finding similar Workflows for Workflow#18
Finding similar Workflows for Workflow#19
Finding similar Workflows for Workflow#20
Finding similar Workflows for Workflow#21
Finding similar Workflows for Workflow#22
Finding similar Workflows for Workflow#24
Finding similar Workflows for Workflow#25
Finding similar Workflows for Workflow#26
F

In [65]:
for each in grouped_workflows:
    print('-' * 50)
    print(len(each))
    for e in each:
        print(e)

--------------------------------------------------
2
Resolving Smoke Detector and Window Sensor Alerts
Resolving Smoke Detector Offline and Failure Alerts
--------------------------------------------------
4
Troubleshooting and Scheduling Technician for Camera Issue
Resolving Camera Connectivity Issue and Scheduling Technician Visit
Scheduling a Technician Visit for Camera Repair
Scheduling a Technician Appointment for Camera and System Setup
--------------------------------------------------
4
New Owner Account Takeover Process
New Owner Takeover Process
Transfer Process for New Owner Takeover
Internal Transfer Process for New Owner Takeover
--------------------------------------------------
2
Offering Alternative Customer Support Options
Offering Customer Support and Self-Help Options
--------------------------------------------------
2
Checking Eligibility for Equipment Upgrade
Product Upgrade Eligibility Check
--------------------------------------------------
3
Checking Contract E

In [67]:
unique_workflow_titles = solo_workflows + [random.choice(w) for w in grouped_workflows]
unique_workflows = [title_to_workflow[w] for w in unique_workflow_titles]
len(unique_workflows)

919

In [83]:
filtered_unique_workflows = [w for w in unique_workflows if len(w['steps']) > 3] # skip too small workflows
len(filtered_unique_workflows)

905

In [84]:
filtered_unique_workflows[0]

{'title': 'Verifying Customer Information and Addressing Contract Expiry Inquiry',
 'steps': ['Greet the customer and introduce yourself.',
  "Ask for the customer's name for personalization.",
  'Correctly address the customer upon clarification (e.g., Mr., Mrs., Miss).',
  'For verification purposes, request the customer to verify their address and the account code word.',
  'If the customer has multiple accounts or addresses, ask for details of each one sequentially.',
  'Confirm the ZIP code and code word for each account mentioned.',
  "Address the primary reason for the customer's call, such as contract expiration inquiry.",
  'If necessary, search for additional accounts to ensure all customer concerns are addressed.',
  'Confirm if the customer is experiencing any issues with the system, such as login problems.',
  'Address any immediate concerns the customer has, such as username and password issues.',
  'Provide the customer with the specific information they requested, such 

In [85]:
for w in filtered_unique_workflows[:10]:
    print(w['title'])

Verifying Customer Information and Addressing Contract Expiry Inquiry
Resolving App Login Issues and Understanding Device Settings Migration
Navigating to the Correct Website for Account Management
Discussing Account Renewal Options and Promotions
Expanding Services to Additional Properties
Call Transfer Process
Enabling Test Mode for Alarm System Maintenance
Troubleshooting a Front Door Camera That Is Not Recording
Resolving Camera Issues for Customers with Pending Installation Status
Workaround for Creating a Ticket When Unable to Select an Option Due to System Restrictions


In [86]:
for w in filtered_unique_workflows:
    print('-' * 100)
    print('\n\n')
    for k, v in w.items():
        if isinstance(v, list):
            val = '\n* '.join(v)
            print(f'{k.capitalize()}:\n* {val}')
        else:
            print(f'{k.capitalize()}: {v}')    

----------------------------------------------------------------------------------------------------



Title: Verifying Customer Information and Addressing Contract Expiry Inquiry
Steps:
* Greet the customer and introduce yourself.
* Ask for the customer's name for personalization.
* Correctly address the customer upon clarification (e.g., Mr., Mrs., Miss).
* For verification purposes, request the customer to verify their address and the account code word.
* If the customer has multiple accounts or addresses, ask for details of each one sequentially.
* Confirm the ZIP code and code word for each account mentioned.
* Address the primary reason for the customer's call, such as contract expiration inquiry.
* If necessary, search for additional accounts to ensure all customer concerns are addressed.
* Confirm if the customer is experiencing any issues with the system, such as login problems.
* Address any immediate concerns the customer has, such as username and password issues.
* Provide

In [87]:
[w['title'] for w in filtered_unique_workflows]

['Verifying Customer Information and Addressing Contract Expiry Inquiry',
 'Resolving App Login Issues and Understanding Device Settings Migration',
 'Navigating to the Correct Website for Account Management',
 'Discussing Account Renewal Options and Promotions',
 'Expanding Services to Additional Properties',
 'Call Transfer Process',
 'Enabling Test Mode for Alarm System Maintenance',
 'Troubleshooting a Front Door Camera That Is Not Recording',
 'Resolving Camera Issues for Customers with Pending Installation Status',
 'Workaround for Creating a Ticket When Unable to Select an Option Due to System Restrictions',
 'Service Transfer Process',
 'Troubleshooting Network Connection for IQ Panel 2',
 'Account Cancellation Process for Assisted Living Situations',
 'Effective Support Call Handling',
 'Exploring Contract Renewal and Warranty Options',
 'Managing Tamper Alerts Post Battery Replacement',
 'Resolving Missing Equipment Shipment',
 'Addressing Early Termination Inquiry',
 'Proces

In [129]:
len(filtered_unique_workflows)

905

# Visitor Flow Discovery

In [146]:
pc_id_to_filtered_agent_workflows = {}
for w in filtered_unique_workflows:
    k = title_to_pc_id[w['title']]
    if k not in pc_id_to_filtered_agent_workflows:
        pc_id_to_filtered_agent_workflows[k] = []        
    pc_id_to_filtered_agent_workflows[k].append(w)
len(pc_id_to_filtered_agent_workflows)

690

In [91]:
chat_id = list(pc_id_to_filtered_agent_workflows.keys())[0]
chat = get_chats_with_ids([chat_id])[0]
str(chat), chat.messages, pc_id_to_filtered_agent_workflows[chat_id]

{"message": "use case id not set, fallback to use profile id care-voice", "name": "greyparrot.common.customers", "asctime": "2024-08-29 00:22:48", "levelname": "WARNING", "filename": "customers.py", "funcName": "__init__", "threadName": "MainThread", "status": "WARNING"}
{"message": "use case id not set, fallback to use profile id care-voice", "name": "greyparrot.common.customers", "asctime": "2024-08-29 00:22:50", "levelname": "WARNING", "filename": "customers.py", "funcName": "__init__", "threadName": "MainThread", "status": "WARNING"}


cmd: cresta-cli connstring -i voice-prod voice-prod brinks-care-voice-FKrGHU -r
cmd: cresta-cli connstring -i voice-prod voice-prod brinks-care-voice -r


('00523c8b-0189-4ac2-a34e-93abdeafa478',
 [[1704293890.721] agent (45a8cdc6b8242514): Thank you for being the best part of Brinks Home. My name is Gustavo. To whom do I have the pleasure of speaking with today?,
  [1704293897.77] visitor (45a8cdc6b8242514): Agustaro. My name is James Blair.,
  [1704293901.591] agent (45a8cdc6b8242514): Thank you for calling Miss Mister Blair?,
  [1704293904.31] visitor (45a8cdc6b8242514): Wire.,
  [1704293904.371] agent (45a8cdc6b8242514): And for verification, Oh, thank you for correcting me. And for verification purposes, can you please verify the address And then the code were under the account?,
  [1704293916.63] visitor (45a8cdc6b8242514): So I I have I'm calling about [NUMBER-SEQ].,
  [1704293920.221] agent (45a8cdc6b8242514): Let's start with the first one. Mhmm. Go ahead.,
  [1704293921.15] visitor (45a8cdc6b8242514): The first address is [NUMBER-SEQ] [NUMBER-SEQ] [NUMBER-SEQ] Barbadian Way, Mount Pleasant, North Carolina,
  [1704293929.63] vis

In [92]:
sampled_chats_map = {str(chat): chat for chat in sampled_chats}
len(sampled_chats_map)

1042

In [101]:
chats_for_visitor_flows = [sampled_chats_map[pc_id] for pc_id in pc_id_to_filtered_agent_workflows.keys()]
len(chats_for_visitor_flows)

690

In [106]:
visitor_flows = extract_flows_from_chats(chats_for_visitor_flows, 'visitor')

{"message": "Starting processing 690 chats with 10 workers", "name": "__main__", "asctime": "2024-08-29 00:41:32", "levelname": "INFO", "filename": "2733958983.py", "funcName": "extract_flows_from_chats", "threadName": "MainThread", "status": "INFO"}
{"message": "Discovering visitor flow in chat 00523c8b-0189-4ac2-a34e-93abdeafa478", "name": "__main__", "asctime": "2024-08-29 00:41:32", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-37 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering visitor flow in chat 02edd6be-6fc7-40f3-9f78-f92bf4010749", "name": "__main__", "asctime": "2024-08-29 00:41:32", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-38 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering visitor flow in chat 019d0f7a-fa77-470a-9eb8-34225e484328", "name": "__main__", "asctime": "2024-08-29 00:41:32", "levelname": "IN

Workflows from 10 extracted!


{"message": "Discovering visitor flow in chat 06611c2b-700e-4943-9b54-b9365e578e54", "name": "__main__", "asctime": "2024-08-29 00:41:53", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-46 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering visitor flow in chat 05fe2dce-903f-4d3f-a046-e697c9b4a674", "name": "__main__", "asctime": "2024-08-29 00:41:53", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-41 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering visitor flow in chat 06c18913-c1e4-4274-aed8-d9d9c0ce6528", "name": "__main__", "asctime": "2024-08-29 00:41:56", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-44 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering visitor flow in chat 06c7a277-4b56-40ef-be87-ffa95c1388d6", "name": "__main__", "asc

Workflows from 20 extracted!


{"message": "Discovering visitor flow in chat 0a5877a3-19f4-4f71-8f94-9c07b594ede1", "name": "__main__", "asctime": "2024-08-29 00:42:11", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-44 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering visitor flow in chat 0b7842a4-0172-4c4b-8b78-abd4e9deaa23", "name": "__main__", "asctime": "2024-08-29 00:42:12", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-41 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering visitor flow in chat 0b34e1b5-7bbc-475a-a21c-04b913529bdb", "name": "__main__", "asctime": "2024-08-29 00:42:16", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-45 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering visitor flow in chat 0ad1ad65-50f8-438a-aabe-5a4f9d099c26", "name": "__main__", "asc

...

Workflows from 670 extracted!


{"message": "Discovering visitor flow in chat aa7b6b4a-534d-4a31-be79-5288a415b665", "name": "__main__", "asctime": "2024-08-29 00:58:04", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-38 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering visitor flow in chat abb10195-c038-41b3-9d01-886a99b3e24e", "name": "__main__", "asctime": "2024-08-29 00:58:06", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-37 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering visitor flow in chat 5f26f651-c658-4c41-b304-3c6487a6b38e", "name": "__main__", "asctime": "2024-08-29 00:58:07", "levelname": "INFO", "filename": "2363125687.py", "funcName": "discover_flow_in_chat", "threadName": "Thread-40 (workflow_labeler_worker)", "status": "INFO"}
{"message": "Discovering visitor flow in chat 0f34c94f-cb49-46ae-bd61-46b993bfa91f", "name": "__main__", "asc

Workflows from 680 extracted!


{"message": "Finished processing all 690 chats", "name": "__main__", "asctime": "2024-08-29 00:58:47", "levelname": "INFO", "filename": "2733958983.py", "funcName": "extract_flows_from_chats", "threadName": "MainThread", "status": "INFO"}


Workflows from 690 extracted!


In [107]:
len(visitor_flows)

690

In [110]:
next(iter(visitor_flows)), visitor_flows[next(iter(visitor_flows))]

('2f849351-5b66-40e5-92f7-bb7ffe26ba86',
 [{'title': 'Canceling a Business Alarm System',
   'steps': ['Call the Brinks Home customer service line.',
    'Provide your first and last name to the account manager.',
    'Mention that the call is regarding the cancellation of a business alarm system.',
    'Provide the address associated with the account when asked.',
    'If asked for a passcode and you do not have it, inform the agent that you do not have it on you but mention you are aware of the account details such as billing information.',
    'Wait for the account manager to transfer you to the correct department for further assistance.']}])

# Visitor Flow Diversification

In [112]:
SYSTEM_PROMPT_VISITOR_WORKFLOW_DIVERSIFICATION = """### Context and data description
You are a conversation analyst working for a Call Center.

You will be given a flow of steps which Customer takes in **a given conversation**. Your goal is to create another Customer Flow which can happen in a similar situation, i.e. similar customer needs.

The flow should be a list of steps which the Customer takes.

The schema of each flow should be as follows:
- **title**: title of the flow
- **steps**: a list of steps which Customer needs to follow

**Important:** Try to think creatively out of box, about what all steps a Customer can take in a similar situation."""

In [116]:
def diversify_visitor_flow(visitor_flow: dict):
    steps_str = '\n* '.join(visitor_flow['steps'])
    visitor_flow_prompt_str = f"Title: {visitor_flow['title']}\nSteps:\n* {steps_str}"
    logger.info(f'Diversifying VisitorFlow flow with title: {visitor_flow["title"]}')
    messages = [
        {
            "role": "system",
            "content": SYSTEM_PROMPT_VISITOR_WORKFLOW_DIVERSIFICATION
        },
        {
            "role": "user",
            "content": visitor_flow_prompt_str
        },
    ]

    # Note: temperature=0.1 to allow for some exploration
    response = chat_completion(model='gpt-4o',
                               messages=messages,
                               temperature=0.1,
                               top_p=1.0,
                               max_tokens=2048,
                               n=1)
    res_workflow_str = response.choices[0].message.content

    messages = [{
        "role": "system",
        "content": SYSTEM_PROMPT_PARSE_WORKFLOW
    }, {
        "role": "user",
        "content": res_workflow_str
    }]

    # TODO need a separate open_ai_client for mini if using Azure
    response = chat_completion(model='gpt-4o-mini-2024-07-18',
                               messages=messages,
                               temperature=0.0,
                               top_p=1.0,
                               max_tokens=2048,
                               n=1,
                               response_format={"type": "json_object"})
    parsed_workflow_str = response.choices[0].message.content

    # TODO define a JSON schema and handle this to make sure the required structure is respected
    return json.loads(parsed_workflow_str)

In [125]:
def diversified_visitor_flow(visitor_flow: dict, iterations: int = 3):
    visitor_flows = [visitor_flow] * iterations
    lock = threading.Lock()
    indexes = queue.Queue()

    diversified_visitor_flows = []
    for idx in range(len(visitor_flows)):
        indexes.put(idx)

    def diversify_labeler_worker():
        while True:
            try:
                idx = indexes.get(block=False)
            except queue.Empty:
                return
            flow = visitor_flows[idx]
            try:
                diversified_flow = diversify_visitor_flow(flow)
                with lock:                    
                    diversified_visitor_flows.append(diversified_flow)
            except Exception as e:
                logger.warning(e, json.dumps(visitor_flow))
            indexes.task_done()

    logger.info(
        f'Starting processing {len(visitor_flows)} flows with {iterations} workers')
    workers = [
        threading.Thread(target=diversify_labeler_worker)
        for _ in range(iterations)
    ]
    for worker in workers:
        worker.start()
    for worker in workers:
        worker.join()
    logger.info(f'Finished processing all {len(visitor_flows)} flows')

    return diversified_visitor_flows

In [166]:
len(pc_id_to_filtered_agent_workflows), len(visitor_flows)

(690, 690)

In [162]:
agent_visitor_simulations = []
for pc_id, v_flows in visitor_flows.items():
    print('-' * 100)
    print(pc_id)
    print(f'Visitor: {[w["title"] for w in v_flows]}')
    print(f'Agent: {[w["title"] for w in pc_id_to_filtered_agent_workflows[pc_id]]}')
    agent_visitor_simulations.append({'chat_id': pc_id, 'agent_workflows': pc_id_to_filtered_agent_workflows[pc_id], 'visitor_flows': [{'original': v_flow, 'diversified': diversified_visitor_flow(v_flow)} for v_flow in v_flows]})

{"message": "Starting processing 3 flows with 3 workers", "name": "__main__", "asctime": "2024-08-29 04:18:05", "levelname": "INFO", "filename": "471917116.py", "funcName": "diversified_visitor_flow", "threadName": "MainThread", "status": "INFO"}
{"message": "Diversifying VisitorFlow flow with title: Canceling a Business Alarm System", "name": "__main__", "asctime": "2024-08-29 04:18:05", "levelname": "INFO", "filename": "3019558530.py", "funcName": "diversify_visitor_flow", "threadName": "Thread-92 (diversify_labeler_worker)", "status": "INFO"}
{"message": "Diversifying VisitorFlow flow with title: Canceling a Business Alarm System", "name": "__main__", "asctime": "2024-08-29 04:18:05", "levelname": "INFO", "filename": "3019558530.py", "funcName": "diversify_visitor_flow", "threadName": "Thread-93 (diversify_labeler_worker)", "status": "INFO"}
{"message": "Diversifying VisitorFlow flow with title: Canceling a Business Alarm System", "name": "__main__", "asctime": "2024-08-29 04:18:05"

----------------------------------------------------------------------------------------------------
2f849351-5b66-40e5-92f7-bb7ffe26ba86
Visitor: ['Canceling a Business Alarm System']
Agent: ['Call Transfer Process']


{"message": "Finished processing all 3 flows", "name": "__main__", "asctime": "2024-08-29 04:18:09", "levelname": "INFO", "filename": "471917116.py", "funcName": "diversified_visitor_flow", "threadName": "MainThread", "status": "INFO"}
{"message": "Starting processing 3 flows with 3 workers", "name": "__main__", "asctime": "2024-08-29 04:18:09", "levelname": "INFO", "filename": "471917116.py", "funcName": "diversified_visitor_flow", "threadName": "MainThread", "status": "INFO"}
{"message": "Diversifying VisitorFlow flow with title: Exploring Options for Account Cancellation and Relocation", "name": "__main__", "asctime": "2024-08-29 04:18:09", "levelname": "INFO", "filename": "3019558530.py", "funcName": "diversify_visitor_flow", "threadName": "Thread-95 (diversify_labeler_worker)", "status": "INFO"}
{"message": "Diversifying VisitorFlow flow with title: Exploring Options for Account Cancellation and Relocation", "name": "__main__", "asctime": "2024-08-29 04:18:09", "levelname": "INFO"

----------------------------------------------------------------------------------------------------
f03514a2-7e5d-4318-bed6-17eada2b7fd2
Visitor: ['Exploring Options for Account Cancellation and Relocation']
Agent: ['Service Transfer Process']


{"message": "Finished processing all 3 flows", "name": "__main__", "asctime": "2024-08-29 04:18:16", "levelname": "INFO", "filename": "471917116.py", "funcName": "diversified_visitor_flow", "threadName": "MainThread", "status": "INFO"}
{"message": "Starting processing 3 flows with 3 workers", "name": "__main__", "asctime": "2024-08-29 04:18:16", "levelname": "INFO", "filename": "471917116.py", "funcName": "diversified_visitor_flow", "threadName": "MainThread", "status": "INFO"}
{"message": "Diversifying VisitorFlow flow with title: Procedure for Canceling a Contract Due to Assisted Living Situation", "name": "__main__", "asctime": "2024-08-29 04:18:16", "levelname": "INFO", "filename": "3019558530.py", "funcName": "diversify_visitor_flow", "threadName": "Thread-98 (diversify_labeler_worker)", "status": "INFO"}
{"message": "Diversifying VisitorFlow flow with title: Procedure for Canceling a Contract Due to Assisted Living Situation", "name": "__main__", "asctime": "2024-08-29 04:18:16",

...

{"message": "Finished processing all 3 flows", "name": "__main__", "asctime": "2024-08-29 06:55:54", "levelname": "INFO", "filename": "471917116.py", "funcName": "diversified_visitor_flow", "threadName": "MainThread", "status": "INFO"}
{"message": "Starting processing 3 flows with 3 workers", "name": "__main__", "asctime": "2024-08-29 06:55:54", "levelname": "INFO", "filename": "471917116.py", "funcName": "diversified_visitor_flow", "threadName": "MainThread", "status": "INFO"}
{"message": "Diversifying VisitorFlow flow with title: Troubleshooting Email Verification and Password Reset on Brinks Home Website", "name": "__main__", "asctime": "2024-08-29 06:55:54", "levelname": "INFO", "filename": "3019558530.py", "funcName": "diversify_visitor_flow", "threadName": "Thread-4142 (diversify_labeler_worker)", "status": "INFO"}
{"message": "Diversifying VisitorFlow flow with title: Troubleshooting Email Verification and Password Reset on Brinks Home Website", "name": "__main__", "asctime": "2

----------------------------------------------------------------------------------------------------
6b6cc711-2825-4ba7-a881-8f3c685e9cc5
Visitor: ['Addressing a Faulty Sensor Issue', 'Customer Attempts to Troubleshoot Sensor Issue']
Agent: ['Handling Faulty Sensor Replacement Request']


{"message": "Finished processing all 3 flows", "name": "__main__", "asctime": "2024-08-29 06:56:07", "levelname": "INFO", "filename": "471917116.py", "funcName": "diversified_visitor_flow", "threadName": "MainThread", "status": "INFO"}
{"message": "Starting processing 3 flows with 3 workers", "name": "__main__", "asctime": "2024-08-29 06:56:07", "levelname": "INFO", "filename": "471917116.py", "funcName": "diversified_visitor_flow", "threadName": "MainThread", "status": "INFO"}
{"message": "Diversifying VisitorFlow flow with title: Customer Attempts to Troubleshoot Sensor Issue", "name": "__main__", "asctime": "2024-08-29 06:56:07", "levelname": "INFO", "filename": "3019558530.py", "funcName": "diversify_visitor_flow", "threadName": "Thread-4148 (diversify_labeler_worker)", "status": "INFO"}
{"message": "Diversifying VisitorFlow flow with title: Customer Attempts to Troubleshoot Sensor Issue", "name": "__main__", "asctime": "2024-08-29 06:56:07", "levelname": "INFO", "filename": "30195

----------------------------------------------------------------------------------------------------
c202c7ed-e36a-4002-af6e-f92a4f963097
Visitor: ['Troubleshooting Beeping Sound and Connectivity Issue on Security Panel', 'Updating Wi-Fi Settings on Security Panel After Changing Internet Providers']
Agent: ['Resolving Alarm Panel Beeping and Connectivity Issues']


{"message": "Finished processing all 3 flows", "name": "__main__", "asctime": "2024-08-29 06:56:24", "levelname": "INFO", "filename": "471917116.py", "funcName": "diversified_visitor_flow", "threadName": "MainThread", "status": "INFO"}
{"message": "Starting processing 3 flows with 3 workers", "name": "__main__", "asctime": "2024-08-29 06:56:24", "levelname": "INFO", "filename": "471917116.py", "funcName": "diversified_visitor_flow", "threadName": "MainThread", "status": "INFO"}
{"message": "Diversifying VisitorFlow flow with title: Updating Wi-Fi Settings on Security Panel After Changing Internet Providers", "name": "__main__", "asctime": "2024-08-29 06:56:24", "levelname": "INFO", "filename": "3019558530.py", "funcName": "diversify_visitor_flow", "threadName": "Thread-4154 (diversify_labeler_worker)", "status": "INFO"}
{"message": "Diversifying VisitorFlow flow with title: Updating Wi-Fi Settings on Security Panel After Changing Internet Providers", "name": "__main__", "asctime": "202

In [163]:
random.shuffle(agent_visitor_simulations)

In [164]:
len(agent_visitor_simulations)

690

In [197]:
agent_visitor_simulations[0]

{'chat_id': '6f3e6a09-f83a-404a-b7cd-d85ce7b420c3',
 'agent_workflows': [{'title': 'Resolving User Account Access and Master Code Issues',
   'steps': ["Greet the Customer and Verify Identity: Start the conversation by thanking the customer for calling and introduce yourself. Ask for the customer's name and verify their identity by asking for their address and a security code or the last four digits of their social security number.",
    "Understand the Issue: Listen to the customer's problem regarding their inability to access their user accounts or specific settings within their security system.",
    "Verify Account Details: Confirm the details of the customer's account, including the correct code word or PIN associated with the account.",
    'Reset or Provide Temporary Access: If the customer is unable to access their account or certain functionalities, offer to reset their account from your end or provide a temporary master code that allows them to reconfigure their settings.',
 

In [177]:
get_chats_with_ids([agent_visitor_simulations[0]['chat_id']])[0].messages

{"message": "use case id not set, fallback to use profile id care-voice", "name": "greyparrot.common.customers", "asctime": "2024-08-29 13:29:28", "levelname": "WARNING", "filename": "customers.py", "funcName": "__init__", "threadName": "MainThread", "status": "WARNING"}
{"message": "use case id not set, fallback to use profile id care-voice", "name": "greyparrot.common.customers", "asctime": "2024-08-29 13:29:28", "levelname": "WARNING", "filename": "customers.py", "funcName": "__init__", "threadName": "MainThread", "status": "WARNING"}


cmd: cresta-cli connstring -i voice-prod voice-prod brinks-care-voice-FKrGHU -r
cmd: cresta-cli connstring -i voice-prod voice-prod brinks-care-voice -r


[[1704223275.316] visitor (66e197cc89b260e7): Risk. Technical support.,
 [1704223277.039] agent (66e197cc89b260e7): Thank for being the best part of Brinks Home. My name is Michelle. Who do I have the pleasure of speaking with?,
 [1704223283.398] visitor (66e197cc89b260e7): Generic screenshot, but I can barely hear you.,
 [1704223286.449] agent (66e197cc89b260e7): Are you able to hear me now mail?,
 [1704223293.638] visitor (66e197cc89b260e7): I think my volume. Let me see if I can hear my volume. Okay. Hello?,
 [1704223296.629] agent (66e197cc89b260e7): Is that better?,
 [1704223297.749] agent (66e197cc89b260e7): No problem.,
 [1704223297.838] visitor (66e197cc89b260e7): Yeah. That's better. Thank you.,
 [1704223300.379] agent (66e197cc89b260e7): Could you,
 [1704223300.698] visitor (66e197cc89b260e7): So mine is generic.,
 [1704223301.989] agent (66e197cc89b260e7): Thank you. Could you verify the address for security purpose.,
 [1704223306.468] visitor (66e197cc89b260e7): 19 o 3 Java

In [199]:
for w in agent_visitor_simulations[0]['agent_workflows']:
    print(f'**AGENT**:')
    print_workflow(w)
for w in agent_visitor_simulations[0]['visitor_flows']:
    print(f'**VISITOR**:')
    for k, v in w.items():
        print(f'**{k.capitalize()}**:')
        if isinstance(v, dict):
            print_workflow(v)
        elif isinstance(v, list):
            for each in v:
                print_workflow(each)

**AGENT**:
Title: Resolving User Account Access and Master Code Issues
Steps:
* Greet the Customer and Verify Identity: Start the conversation by thanking the customer for calling and introduce yourself. Ask for the customer's name and verify their identity by asking for their address and a security code or the last four digits of their social security number.
* Understand the Issue: Listen to the customer's problem regarding their inability to access their user accounts or specific settings within their security system.
* Verify Account Details: Confirm the details of the customer's account, including the correct code word or PIN associated with the account.
* Reset or Provide Temporary Access: If the customer is unable to access their account or certain functionalities, offer to reset their account from your end or provide a temporary master code that allows them to reconfigure their settings.
* Instruct on How to Use the Master Code: Explain to the customer how to use the master cod

# Save simulations

In [205]:
len(agent_visitor_simulations2)

690

In [213]:
task = 'simulations'
output_filename = f'/src/chat-ai/notebooks/virtual-agent/{customer_name}_{task}_{get_timestamp_as_version()}_train.jsonl'
print(output_filename)
save_jsonl_file(agent_visitor_simulations2, output_filename)

/src/chat-ai/notebooks/virtual-agent/brinks-care-voice_simulations_082920241355579600_train.jsonl
